# IMPORTAR LIBRERIAS

In [1]:
#from analystcommunity.apricot_manager import get_json_by_request_id, execute_simulation,get_df_by_dic,get_demand_forecast_error,change_sigma_demand_forecast_error,update_dic_with_forecast_error
import pandas as pd
from analystcommunity import read_connection_data_warehouse as dr
import analystcommunity

from procurement_lib import redash
import procurement_lib as plib


import json
import seaborn as sns
import matplotlib.pyplot as plt
import pandas as pd
from scipy.stats import skew
import boto3
import pandas as pd
import json
import os
import requests
import uuid
from procurement_lib import redash

import ast
import math
from scipy.stats import norm
import numpy as np
from scipy.signal import savgol_filter



import pytz



import seaborn as sns
import matplotlib.pyplot as plt
from tqdm import tqdm

###########

import sys
import os


project_root = os.path.abspath('/home/jupyter-supply_planning/analytics_inventory-transfers-model')
sys.path.append(project_root)


from app.src.container import Container
from app.src.classes import Supplier, Product, TranshipmentProblem
from dotenv import load_dotenv
load_dotenv()

import json
from datetime import datetime, timedelta

from procurement_lib import redash
import procurement_lib as plib
redash = plib.Redash(os.getenv('BASE_URL'), os.getenv('API_KEY'))

######

c = Container()
stock_service = c.available_stock_service()
forecast_client = c.get_dp_forecast_client()
mlopsclient = c.get_mlops_client()






In [2]:
########## CONFIGURATION #####

In [3]:
configuration_name= 'GRU_to_STA'
region_code = 'SPO'

superbodegas = ['ARFRIO', 'GRU'] #Bodegas que tambien son superbodegas, va el coigo de la bodega. 

# CLASS: TranshipmentProblem

In [4]:
transhipment_configurations = {
    'STA_to_GRU': {
        'origin_warehouse': 'STA',
        'destination_warehouse': 'GRU',
        'transhipment_lead_time_probability': {1: 1.0},
    },
    'GRU_to_STA': {
        'origin_warehouse': 'GRU',
        'destination_warehouse': 'STA',
        'transhipment_lead_time_probability': {1: 1.0},
    },
    'STA_to_VLP': {
        'origin_warehouse': 'STA',
        'destination_warehouse': 'VLP',
        'transhipment_lead_time_probability': {1: 1.0},
    },
    'VLP_to_STA': {
        'origin_warehouse': 'VLP',
        'destination_warehouse': 'STA',
        'transhipment_lead_time_probability': {1: 1.0},
    },
    'GRU_to_VLP': {
        'origin_warehouse': 'GRU',
        'destination_warehouse': 'VLP',
        'transhipment_lead_time_probability': {1: 1.0},
    },
    'VLP_to_GRU': {
        'origin_warehouse': 'VLP',
        'destination_warehouse': 'GRU',
        'transhipment_lead_time_probability': {1: 1.0},
    },
}

config_sta_to_gru = transhipment_configurations[configuration_name]
print(config_sta_to_gru)

{'origin_warehouse': 'GRU', 'destination_warehouse': 'STA', 'transhipment_lead_time_probability': {1: 1.0}}


# CLASS: supplier

In [5]:
execution_date = datetime.now().strftime("%Y-%m-%d")
lead_times_data = mlopsclient.get_lead_times(warehouse_code='STA',execution_date=execution_date)

2024-10-16 17:42:13,261 - frubana_app - INFO - Payload: {"model": "lead_times", "vertical": "planning", "page": 1, "limit": 500, "query": {"condition_type": "AND", "conditions": [{"field": "warehouse_code", "value": "STA", "comparison": "e"}, {"field": "day_of_week", "value": 2, "comparison": "e"}]}, "fields_to_return": ["sku_code", "created_at", "lead_time", "day_of_week", "warehouse_code", "supplier_id"]} (api_clients.py:164)
2024-10-16 17:42:13,688 - frubana_app - INFO - Response: {'result': [{'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'15': 1.0}, 'type': 'DISC'}, 'sku_code': 'BHZ-FRU1-CAT120831-472696:1175218:1175217:653063', 'supplier_id': 6542, 'warehouse_code': 'STA'}, {'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'15': 1.0}, 'type': 'DISC'}, 'sku_code': 'BHZ-FRU1-CAT120831-472697:1175220:1175219:653065', 'supplier_id': 6542, 'warehouse_code': 'STA'}, {'created_at': '2024-10-16T07:03:19',

2024-10-16 17:42:13,693 - frubana_app - INFO - Payload: {"model": "lead_times", "vertical": "planning", "page": 2, "limit": 500, "query": {"condition_type": "AND", "conditions": [{"field": "warehouse_code", "value": "STA", "comparison": "e"}, {"field": "day_of_week", "value": 2, "comparison": "e"}]}, "fields_to_return": ["sku_code", "created_at", "lead_time", "day_of_week", "warehouse_code", "supplier_id"]} (api_clients.py:164)
2024-10-16 17:42:13,924 - frubana_app - INFO - Response: {'result': [{'created_at': '2024-06-19T07:11:52', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'1': 1.0}, 'type': 'DISC'}, 'sku_code': 'SPO-FRU1-CAT106969-59578:121467:121468:72331', 'supplier_id': 1335, 'warehouse_code': 'STA'}, {'created_at': '2024-06-19T07:11:52', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'0': 1.0}, 'type': 'DISC'}, 'sku_code': 'SPO-FRU1-CAT106969-59578:121467:121468:72331', 'supplier_id': 1402, 'warehouse_code': 'STA'}, {'created_at': '2024-06-19T07:11:52', 'day_of_w

2024-10-16 17:42:13,929 - frubana_app - INFO - Payload: {"model": "lead_times", "vertical": "planning", "page": 3, "limit": 500, "query": {"condition_type": "AND", "conditions": [{"field": "warehouse_code", "value": "STA", "comparison": "e"}, {"field": "day_of_week", "value": 2, "comparison": "e"}]}, "fields_to_return": ["sku_code", "created_at", "lead_time", "day_of_week", "warehouse_code", "supplier_id"]} (api_clients.py:164)
2024-10-16 17:42:14,180 - frubana_app - INFO - Response: {'result': [{'created_at': '2024-06-19T07:11:52', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'1': 1.0}, 'type': 'DISC'}, 'sku_code': 'SPO-FRU1-CAT106980-80911:188427:188428:102147', 'supplier_id': 1335, 'warehouse_code': 'STA'}, {'created_at': '2024-06-19T07:11:52', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'5': 1.0}, 'type': 'DISC'}, 'sku_code': 'SPO-FRU1-CAT106980-80911:194627:194628:106278', 'supplier_id': 1588, 'warehouse_code': 'STA'}, {'created_at': '2024-06-19T07:11:52', 'day_of

2024-10-16 17:42:14,185 - frubana_app - INFO - Payload: {"model": "lead_times", "vertical": "planning", "page": 4, "limit": 500, "query": {"condition_type": "AND", "conditions": [{"field": "warehouse_code", "value": "STA", "comparison": "e"}, {"field": "day_of_week", "value": 2, "comparison": "e"}]}, "fields_to_return": ["sku_code", "created_at", "lead_time", "day_of_week", "warehouse_code", "supplier_id"]} (api_clients.py:164)
2024-10-16 17:42:14,412 - frubana_app - INFO - Response: {'result': [{'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'12': 0.3861386138613861, '13': 0.1485148514851485, '14': 0.2277227722772277, '20': 0.0792079207920792, '21': 0.0792079207920792, '22': 0.0792079207920792}, 'type': 'DISC'}, 'sku_code': 'SPO-FRU1-CAT106994-457935:1157396:1157397:633841', 'supplier_id': 5910, 'warehouse_code': 'STA'}, {'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'12': 0.3, '13': 0.1, '15': 0.2,

2024-10-16 17:42:14,417 - frubana_app - INFO - Payload: {"model": "lead_times", "vertical": "planning", "page": 5, "limit": 500, "query": {"condition_type": "AND", "conditions": [{"field": "warehouse_code", "value": "STA", "comparison": "e"}, {"field": "day_of_week", "value": 2, "comparison": "e"}]}, "fields_to_return": ["sku_code", "created_at", "lead_time", "day_of_week", "warehouse_code", "supplier_id"]} (api_clients.py:164)
2024-10-16 17:42:14,659 - frubana_app - INFO - Response: {'result': [{'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'14': 1.0}, 'type': 'DISC'}, 'sku_code': 'SPO-FRU1-CAT107073-197110:480400:480399:243993', 'supplier_id': 3033, 'warehouse_code': 'STA'}, {'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'4': 1.0}, 'type': 'DISC'}, 'sku_code': 'SPO-FRU1-CAT107073-197110:480400:480399:243993', 'supplier_id': 4518, 'warehouse_code': 'STA'}, {'created_at': '2024-10-16T07:03:19', 'day

...

2024-10-16 17:42:18,284 - frubana_app - INFO - Payload: {"model": "lead_times", "vertical": "planning", "page": 19, "limit": 500, "query": {"condition_type": "AND", "conditions": [{"field": "warehouse_code", "value": "STA", "comparison": "e"}, {"field": "day_of_week", "value": 2, "comparison": "e"}]}, "fields_to_return": ["sku_code", "created_at", "lead_time", "day_of_week", "warehouse_code", "supplier_id"]} (api_clients.py:164)
2024-10-16 17:42:18,540 - frubana_app - INFO - Response: {'result': [{'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'1': 0.9, '3': 0.1}, 'type': 'DISC'}, 'sku_code': 'SPO-FRU1-CAT2-44:41:81:82', 'supplier_id': 6348, 'warehouse_code': 'STA'}, {'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'1': 0.9, '3': 0.1}, 'type': 'DISC'}, 'sku_code': 'SPO-FRU1-CAT2-44:41:81:82', 'supplier_id': 6379, 'warehouse_code': 'STA'}, {'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_ti

2024-10-16 17:42:18,544 - frubana_app - INFO - Payload: {"model": "lead_times", "vertical": "planning", "page": 20, "limit": 500, "query": {"condition_type": "AND", "conditions": [{"field": "warehouse_code", "value": "STA", "comparison": "e"}, {"field": "day_of_week", "value": 2, "comparison": "e"}]}, "fields_to_return": ["sku_code", "created_at", "lead_time", "day_of_week", "warehouse_code", "supplier_id"]} (api_clients.py:164)
2024-10-16 17:42:18,886 - frubana_app - INFO - Response: {'result': [{'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'1': 0.94, '3': 0.06}, 'type': 'DISC'}, 'sku_code': 'SPO-FRU1-CAT2-76:73:145:146', 'supplier_id': 500, 'warehouse_code': 'STA'}, {'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'1': 0.94, '3': 0.06}, 'type': 'DISC'}, 'sku_code': 'SPO-FRU1-CAT2-76:73:145:146', 'supplier_id': 594, 'warehouse_code': 'STA'}, {'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'l

2024-10-16 17:42:18,891 - frubana_app - INFO - Payload: {"model": "lead_times", "vertical": "planning", "page": 21, "limit": 500, "query": {"condition_type": "AND", "conditions": [{"field": "warehouse_code", "value": "STA", "comparison": "e"}, {"field": "day_of_week", "value": 2, "comparison": "e"}]}, "fields_to_return": ["sku_code", "created_at", "lead_time", "day_of_week", "warehouse_code", "supplier_id"]} (api_clients.py:164)
2024-10-16 17:42:19,144 - frubana_app - INFO - Response: {'result': [{'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'1': 1.0}, 'type': 'DISC'}, 'sku_code': 'SPO-FRU1-CAT6-57:54:107:108', 'supplier_id': 4981, 'warehouse_code': 'STA'}, {'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'1': 1.0}, 'type': 'DISC'}, 'sku_code': 'SPO-FRU1-CAT6-57:54:107:108', 'supplier_id': 5045, 'warehouse_code': 'STA'}, {'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_valu

2024-10-16 17:42:19,148 - frubana_app - INFO - Payload: {"model": "lead_times", "vertical": "planning", "page": 22, "limit": 500, "query": {"condition_type": "AND", "conditions": [{"field": "warehouse_code", "value": "STA", "comparison": "e"}, {"field": "day_of_week", "value": 2, "comparison": "e"}]}, "fields_to_return": ["sku_code", "created_at", "lead_time", "day_of_week", "warehouse_code", "supplier_id"]} (api_clients.py:164)
2024-10-16 17:42:19,562 - frubana_app - INFO - Response: {'result': [{'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'14': 1.0}, 'type': 'DISC'}, 'sku_code': 'VCP-FRU1-CAT146982-325929:818738:818737:430806', 'supplier_id': 4312, 'warehouse_code': 'STA'}, {'created_at': '2024-10-16T07:03:19', 'day_of_week': 2, 'lead_time': {'prob_value_pairs': {'14': 1.0}, 'type': 'DISC'}, 'sku_code': 'VCP-FRU1-CAT146982-326624:818554:818553:430684', 'supplier_id': 1889, 'warehouse_code': 'STA'}, {'created_at': '2024-10-16T07:03:19', 'd

2024-10-16 17:42:19,564 - frubana_app - INFO - Payload: {"model": "lead_times", "vertical": "planning", "page": 23, "limit": 500, "query": {"condition_type": "AND", "conditions": [{"field": "warehouse_code", "value": "STA", "comparison": "e"}, {"field": "day_of_week", "value": 2, "comparison": "e"}]}, "fields_to_return": ["sku_code", "created_at", "lead_time", "day_of_week", "warehouse_code", "supplier_id"]} (api_clients.py:164)
2024-10-16 17:42:19,810 - frubana_app - INFO - Response: {'result': []} (api_clients.py:166)


In [6]:
#lead_times_data

In [7]:
# Crear el payload
seen_external_ids = set()
supplier_payload = []

suppliers = []

for key, lead_time_model in lead_times_data.items():
    external_id = str(key[1]) 
    
    if external_id not in seen_external_ids:
        supplier_data = Supplier(
            external_id=external_id,
            lead_time_model=dict(lead_time_model),
            delay_model={}  # Por defecto es un diccionario vacío
        )
        suppliers.append(supplier_data)
        seen_external_ids.add(external_id)

supplier_payload = [supplier._to_dict() for supplier in suppliers]

# Imprimir el payload final
#print(supplier_payload)

In [8]:
#supplier_dicts = [supplier._to_dict() for supplier in suppliers]

# Convertir la lista de diccionarios a un DataFrame
#supplier_df = pd.DataFrame(supplier_dicts)

#supplier_df


# METODOS

In [9]:
def get_product_lits(): #D1T
    query = f"""

with base_ean as (
    select
    'SPO' as region_code,
    CODIGO,
    PATRON_ALIAS,
    PATRON_ALIAS as ean
    -- LEFT(RIGHT(ean,LENGTH(ean)-2),LENGTH(ean)-3) as ean
    from (
    select -- distinct
    CODIGO,
    PATRON_ALIAS,
    SUBSTRING(PATRON_ALIAS,POSITION('|^' IN PATRON_ALIAS),LENGTH(PATRON_ALIAS)) as ean
    from mysql_pepo_data."invas_frubana_br.producto_master"
    ) a
)

,microcats as (
    SELECT DISTINCT
        sku.region,
        sku.parent_sku,
        sku.parent_product_id,
        sku.parent_name,
        sku.child_sku,
        sku.child_product_id,
        sku.child_name,
        child_units_per_parent_unit
        --,cat.status
    FROM postgres_main_federate."ops_demand_planning.sku_validations.sku_child_parent_historical_relationships" sku
    LEFT JOIN lnd_ops.dp_product_catalog cat ON  sku.region = cat.region_code And sku.parent_product_id = cat.product_id
    
    WHERE sku.sku_mapping_type = 1
    AND cat.status = 'ON'
)



    SELECT DISTINCT
        p.region_code,
        p.sku,
        p.product_id,
        --p.frida_id,
        --p.name as product_name,
        p.product_category_id,
        c.name as category,
        pc.name as subcategory,
        --COALESCE(CAST(p.ean AS VARCHAR),be.ean) as ean,
        --p.buy_unit,
        --s.id as supplier_id,
        --s.name as supplier_name,
        --TRIM(SPLIT_PART(s.name,'(',1)) as supplier_general_name,
        --sc.name as supplier_category,
        --r.name as category_manager,
        m.parent_product_id as microcat_id
        --m.parent_name as microcat
        
    FROM postgres_main_co."purchase_orders.products" as p
    JOIN postgres_main_co."purchase_orders.product_categories" as c on c.id = p.product_category_id
    LEFT JOIN postgres_procurement."pr_purchases.purchase_order_item" as poi on poi.sku = p.sku
    LEFT JOIN postgres_procurement."pr_purchases.purchase_order" as po on po.id = poi.purchase_order_id
    LEFT JOIN postgres_main_co."purchase_orders.suppliers" as s on s.id = po.supplier_id
    LEFT JOIN postgres_main_co."purchase_orders.categories" as sc on sc.id = s.category_id
    LEFT JOIN postgres_main_co."purchase_orders.responsibles" as r on r.id = s.responsible_id
    LEFT JOIN postgres_main_co."purchase_orders.pricing_categories" as pc on pc.id = p.pricing_category_id
    LEFT JOIN base_ean as be on be.codigo = p.sku
    LEFT JOIN microcats as m on m.child_sku = p.sku
    
    WHERE p.region_code in ('SPO')
    --AND p.product_category_id in (5,6,7,8,9,10,13,18)
    AND p.deleted_at is null
    AND p.parent_id is null
    AND JSON_EXTRACT_PATH_TEXT(p.purchases,'out') = 'true'
    AND po.delivery_date >= DATE_TRUNC('MONTH', DATE(GETDATE() AT TIME ZONE 'UTC' AT TIME ZONE 'America/Sao_Paulo') - INTERVAL '4 MONTH')


    """
    df=dr.run_read_prod_query(query)
    return df

def get_superwarehouse_prodcut_list():
    query = f"""
    
SELECT
  DISTINCT *
FROM
  (
    SELECT
      s.sku,
      SPLIT_PART(s.sku, ':', 4) AS product_id,
      w.code AS warehouse,
      --CASE
    --    WHEN w.code = 'SGRU' THEN 'GRU'
      --  WHEN w.code = 'SCONT' THEN 'CONT'
    --    WHEN w.code = 'SARFRIO' THEN 'ARFRIO'
     --   ELSE w.code
      --END AS warehouse_join,
      --p.name,
      --r.email,
      --c.coverage_period AS coverage_period_actual,
      --c.service_level AS service_level_actual,
      --c.on_for_apricot,
      --c.strategy_type,
      --p.region_code,
      --pc.name as category,
      --CAST(
    --    json_extract_path_text(p.purchases, 'out') AS VARCHAR
     -- ) AS out,
      ROW_NUMBER() OVER(
        PARTITION BY s.sku,
        c.warehouse
        ORDER BY
          c.updated_at DESC
      ) AS rn
    FROM
      postgres_procurement."pr_apricot.skus" s
      LEFT JOIN postgres_procurement."pr_apricot.apricot_configurations" c ON s.id = sku_id
      LEFT JOIN postgres_procurement."pr_apricot.warehouse_groups" w ON c.warehouse_group_id = w.id
      LEFT JOIN postgres_procurement."pr_apricot.responsibles" r ON c.responsible_id = r.id
      LEFT JOIN postgres_main_co."purchase_orders.products" p ON s.sku = p.sku
      LEFT JOIN postgres_main_co."purchase_orders.product_categories" pc on pc.id = p.product_category_id
    WHERE
      c.deleted_at IS NULL
      AND c.on_for_apricot = 'true'
      --AND CAST(
        --    json_extract_path_text(p.purchases, 'out') AS VARCHAR
      --) = 'true'
      AND p.region_code IN ('SPO')
      AND w.code IN ('SGRU') --,'SARFRIO'
  )
WHERE
  rn = 1

    """
    df=dr.run_read_prod_query(query)
    return df

def get_last_cost_and_supp_id(): 
    query = f"""
        WITH compras AS (
          SELECT
            DISTINCT purchase_order.product_id,
            purchase_order.supplier_id
          FROM
            postgres_main_co."purchase_orders.purchase_orders" purchase_order -- Seleccionamos la última compra por producto
          WHERE
            DATE(created_at) = (
              SELECT
                MAX(DATE(po.created_at))
              FROM
                postgres_main_co."purchase_orders.purchase_orders" po
              WHERE
                po.product_id = purchase_order.product_id
            )
        ),
        base AS (
          SELECT
            p.region_code,
            p.sku,
            pr.price,
            row_number() OVER (
              PARTITION BY p.sku
              ORDER BY
                pr.updated_at DESC
            ) AS row,
            c.supplier_id
          FROM
            postgres_main_co."purchase_orders.prices" pr
            INNER JOIN postgres_main_co."purchase_orders.products" p ON pr.product_id = p.id
            INNER JOIN postgres_main_co."purchase_orders.product_categories" pc ON pc.id = p.product_category_id
            INNER JOIN compras c ON c.product_id = pr.product_id
          WHERE
            pr.price > 0
            AND pr.deleted_at IS NULL
            AND p.deleted_at IS NULL
            AND p.parent_id IS NULL
            AND p.purchases IS NOT NULL
            AND DATE(pr.updated_at) <= (
              SELECT
                MAX(DATE(pr2.updated_at))
              FROM
                postgres_main_co."purchase_orders.prices" pr2
              WHERE
                pr2.product_id = pr.product_id
            )
        ),
        final_prices AS (
          SELECT
            base.sku,
            base.region_code,
            base.supplier_id,
            AVG(base.price) AS avg_price
          FROM
            base
          WHERE
            row = 1
          GROUP BY
            base.sku,
            base.region_code,
            base.supplier_id
        )
        SELECT
          sku,
          region_code,
          supplier_id AS suppliers,
          ROUND(avg_price, 2) AS current_price_per_unit
        FROM
          final_prices
    """
    df=dr.run_read_prod_query(query)
    return df

def get_service_level(): 
    query = f"""
          SELECT
          DISTINCT
            *
          FROM
            (
              SELECT
                s.sku,
                --SPLIT_PART(s.sku, ':', 4) AS product_id,
                w.code AS warehouse,
                --p.name,
                --r.email,
                --c.coverage_period AS coverage_period_actual,
                c.service_level AS desired_service_level,
                --c.on_for_apricot,
                --c.strategy_type,
                p.region_code,
                --pc.name as category,
                --CAST(
                --  json_extract_path_text(p.purchases, 'out') AS VARCHAR
                --) AS out,
                ROW_NUMBER() OVER(
                  PARTITION BY s.sku,
                  c.warehouse
                  ORDER BY
                    c.updated_at DESC
                ) AS rn
              FROM
                postgres_procurement."pr_apricot.skus" s
                LEFT JOIN postgres_procurement."pr_apricot.apricot_configurations" c ON s.id = sku_id
                LEFT JOIN postgres_procurement."pr_apricot.warehouse_groups" w ON c.warehouse_group_id = w.id
                LEFT JOIN postgres_procurement."pr_apricot.responsibles" r ON c.responsible_id = r.id
                LEFT JOIN postgres_main_co."purchase_orders.products" p ON s.sku = p.sku
                LEFT JOIN postgres_main_co."purchase_orders.product_categories" pc on pc.id = p.product_category_id
              WHERE
                c.deleted_at IS NULL
                AND c.on_for_apricot = 'true'
                AND p.region_code IN ('SPO')

            )
          WHERE
            rn = 1
    """
    df=dr.run_read_prod_query(query)
    return df

# CLASS: Prodcuct

In [10]:
def generate_payload(row, supplier_payload):
    # Crear lista de Supplier a partir de external_ids usando supplier_payload
    suppliers = []
    for external_id in row['suppliers']:
        # Buscar el supplier en supplier_payload usando el external_id
        supplier_info = next((supplier for supplier in supplier_payload if supplier['external_id'] == external_id), None)
        
        # Si encontramos el supplier, usamos su lead_time_model
        if supplier_info:
            supplier = Supplier(
                external_id=supplier_info['external_id'],
                lead_time_model=supplier_info['lead_time_model'],  # Usar los datos de supplier_payload
                delay_model=supplier_info['delay_model']  # Usar delay_model de supplier_payload
            )
        else:
            # Si no encontramos el supplier, creamos un supplier vacío
            supplier = Supplier(
                external_id=external_id,
                lead_time_model={},  # Dejar vacío si no hay datos
                delay_model={}  # Dejar delay_model vacío
            )
        suppliers.append(supplier)

    # Crear el payload del producto con los suppliers
    payload = {
        'sku': str(row['sku']),
        'warehouse': str(row['warehouse']),
        'desired_service_level': float(row['desired_service_level']),
        'days_to_next_review': int(row['days_to_next_review']),
        'units_per_product_dim': int(row['units_per_product_dim']),
        'supplier_dim_to_product_dim_conversion_factor': float(row['supplier_dim_to_product_dim_conversion_factor']),
        'current_inventory': int(row['current_inventory']),
        'detailed_incoming_inventory': dict(row['detailed_incoming_inventory']),
        'forecast': dict(row['forecast']),
        'forecast_error_model': dict(row['forecast_error_model']),
        'current_price_per_unit': float(row['current_price_per_unit']),
        'percentage_cost_per_unit_excess': float(row['percentage_cost_per_unit_excess']),
        'percentage_cost_per_unit_shortage': float(row['percentage_cost_per_unit_shortage']),
        'mandatory': bool(row['mandatory']),
        'suppliers': [supplier._to_dict() for supplier in suppliers]  # Lista de suppliers en formato dict
    }
    return payload

def generate_product_payload(transhipment_configurations, configuration_name, supplier_payload):
    configuration = transhipment_configurations[configuration_name]

    # Inicializar lista para los payloads de origen y destino
    origin_payload = []
    destination_payload = []

    for warehouse_type in ['origin_warehouse', 'destination_warehouse']:
        warehouse_code = configuration[warehouse_type]
        
        product_list = get_product_lits()
        
        product_list['warehouse'] = warehouse_code

        ###### PRODUCT ID SKU & LISTS #########
        product_ids = product_list['product_id'].astype('int').tolist()
        skus = product_list['sku'].tolist()

        # Fechas de hoy y una semana después
        start_date = datetime.now().strftime('%Y-%m-%d')
        end_date = (datetime.now() + timedelta(weeks=1)).strftime('%Y-%m-%d')

        ######## INVENTORY ########
        inventories = []
        chunk_size = len(product_ids)

        for i in range(0, len(product_ids), chunk_size):
            product_ids_chunk = product_ids[i:i + chunk_size]
            stock_data = stock_service.get_available_stock(warehouse_code, product_ids_chunk)

            for product_id in product_ids_chunk:
                sku_key = next((sku for sku in stock_data.keys() if sku.split(':')[-1] == str(product_id)), None)
                if sku_key:
                    inventory = stock_data.get(sku_key, None)
                else:
                    inventory = None
                inventories.append(inventory)

        product_list['current_inventory'] = inventories
        product_list['current_inventory'].fillna(0, inplace=True)

        ###### IN TRANSIT INVENTORY ######
        in_trasit_service = c.in_transit_stock_service()
        in_transit_data_list = []

        for i in range(0, len(skus), chunk_size):
            sku_chunk = skus[i:i + chunk_size]
            in_transit_stock_data = in_trasit_service.get_detailed_in_transit_stock(
                sku_chunk, warehouse_code, start_date, end_date, excluded_types=None
            )
            for sku in sku_chunk:
                in_transit_data = in_transit_stock_data.get(sku, {})
                in_transit_data_list.append(in_transit_data)

        product_list['detailed_incoming_inventory'] = in_transit_data_list
        product_list['detailed_incoming_inventory'].fillna({}, inplace=True)

        ########## FORECAST ########
        forecast_data_list = []
        date_range = pd.date_range(start=start_date, end=end_date).strftime('%Y-%m-%d').tolist()
        default_forecast = {date: 0.0 for date in date_range}

        for i in range(0, len(product_ids), chunk_size):
            product_ids_chunk = product_ids[i:i + chunk_size]
            params = {
                'warehouse_code': warehouse_code,
                'region_code': region_code,
                'start_date': start_date,
                'end_date': end_date,
                'product_ids': product_ids_chunk
            }
            forecast_data = forecast_client.get_batch_forecasts_skus(params)
            for product_id in product_ids_chunk:
                forecast = forecast_data.get(product_id, default_forecast.copy())
                forecast_data_list.append(forecast)

        product_list['forecast'] = forecast_data_list

        ##### ERROR DE FORECAST ######
        forecast_error_list = []
        forecast_errors_data = mlopsclient.get_forecast_errors(warehouse_code)

        for sku in skus:
            forecast_error = forecast_errors_data.get(sku, {'distribution': 'NORM', 'mu': 0, 'sigma': 0.0001})
            forecast_error_list.append(forecast_error)

        product_list['forecast_error_model'] = forecast_error_list

        ######### IS IN SUPERWAREHOUSE ##########
        if warehouse_type == 'origin_warehouse' and warehouse_code in superbodegas:
            superwarehouse_prodcut_list = get_superwarehouse_prodcut_list()
            superwarehouse_skus = superwarehouse_prodcut_list['sku'].tolist()
            product_list['mandatory'] = product_list['sku'].isin(superwarehouse_skus)
        else:
            product_list['mandatory'] = False

        ######### COSTS AND LAST SUPPLIER ####
        last_cost_and_supp_id = get_last_cost_and_supp_id()
        product_list = pd.merge(product_list, last_cost_and_supp_id[['sku', 'region_code', 'current_price_per_unit', 'suppliers']], on=['sku', 'region_code'], how='left')
        product_list['suppliers'] = product_list['suppliers'].apply(lambda x: [str(int(x))] if pd.notnull(x) else [])
        
        ####### SERVICE LEVEL ####
        service_level = get_service_level()
        product_list = pd.merge(product_list, service_level[['sku', 'warehouse', 'desired_service_level']], on=['sku', 'warehouse'], how='left')
        default_service_level = 0.90
        product_list['desired_service_level'].fillna(default_service_level, inplace=True)

        ############ PERCENTAGE PER UNIT EXCESS ############
        product_list['percentage_cost_per_unit_excess'] = 100.00

        ############ PERCENTAGE PER UNIT SHORTAGE ############
        product_list['percentage_cost_per_unit_shortage'] = 30.00 

        ############ SUPP DIM TO PRODUCT DIM CONVERSION FACTOR ############
        product_list['supplier_dim_to_product_dim_conversion_factor'] = 1.00

        ############ UNITS PER PRODUCTS DIM ############
        product_list['units_per_product_dim'] = 1.00

        ######## DAYS TO NEXT REVIEW #########
        if warehouse_type == 'origin_warehouse':
            product_list['days_to_next_review'] = 7  # origen siempre 7
            # Guardar el payload de origen
            origin_payload = product_list.apply(lambda row: generate_payload(row, supplier_payload), axis=1).tolist()
        else:
            product_list['days_to_next_review'] = 3  # destino

            # Cambiar los suppliers solo para destino
            product_list['suppliers'] = product_list.apply(lambda row: [
                {
                    "external_id": "-1111",
                    "lead_time_model": {1: 1.0},
                    "delay_model": {}
                }
            ], axis=1)
            
            # Guardar el payload de destino
            destination_payload = product_list.apply(lambda row: generate_payload(row, supplier_payload), axis=1).tolist()

    # Devolver ambos payloads por separado (origen y destino)
    return origin_payload, destination_payload

In [11]:
origin_payload, destination_payload = generate_product_payload(
    transhipment_configurations,  # Las configuraciones de transbordo
    configuration_name,           # Nombre de la configuración
    supplier_payload              # El payload generado para los suppliers
)

2024-10-16 17:42:21,751 - frubana_app - DEBUG - Requesting in transit stock with message: {'skus': ['SPO-FRU1-CAT107026-194566:472172:472171:240410', 'SPO-BRF4956-CAT107075-177070:407360:407359:217683', 'SPO-SEA3104-CAT107115-134148:304647:304648:165976', 'SPO-FRU7704-CAT155019-474862:1178302:1178301:656346', 'SPO-FRU1-CAT106994-469616:1170763:1170762:648603', 'SPO-FRU1-CAT114319-442133:1124242:1124241:615289', 'SPO-FRU1-CAT140017-288675:725544:725543:377280', 'SPO-FRU1-CAT120730-474496:1177818:1177817:655813', 'SPO-FRU1-CAT106980-139971:319718:319717:173913', 'SPO-FRU1-CAT114319-442136:1124447:1124448:615295', 'SPO-FRI3206-CAT111881-133596:303582:303583:165352', 'SPO-PLE7454-CAT107094-292216:733686:733685:382167', 'SPO-FRU1-CAT163043-441912:1123450:1123449:614645', 'SPO-FRU1-CAT107273-473724:1176591:1176592:654586', 'SPO-FRU1-CAT108423-99433:227543:227544:124907', 'SPO-FRU1-CAT120728-474418:1177612:1177611:655607', 'SPO-FRU7704-CAT111887-304511:764056:764055:400347', 'SPO-FRU1-CAT1207

2024-10-16 17:42:22,076 - frubana_app - DEBUG - Response: [{'sku': 'SPO-FRU1-CAT106980-464934:1164344:1164343:642389', 'quantity': 20.0}, {'sku': 'SPO-FRU1-CAT106987-450726:1142385:1142386:625273', 'quantity': 840.0}, {'sku': 'SPO-FRU1-CAT107271-71126:161418:161417:89184', 'quantity': 1040.0}, {'sku': 'SPO-FRU1-CAT1-53:50:99:100', 'quantity': 1314.0}, {'sku': 'SPO-FRU1-CAT2-15:14:27:28', 'quantity': 340.0}, {'sku': 'SPO-FRU1-CAT2-52:49:97:98', 'quantity': 100.0}, {'sku': 'SPO-FRU1-CAT6-114:110:221:222', 'quantity': 175.0}, {'sku': 'SPO-FRU1-CAT6-54:51:101:102', 'quantity': 225.0}, {'sku': 'SPO-FRU1-CAT7-60544:126036:126035:73947', 'quantity': 150.0}] (api_clients.py:387)
2024-10-16 17:42:22,291 - frubana_app - DEBUG - Requesting in transit stock with message: {'skus': ['SPO-FRU1-CAT107026-194566:472172:472171:240410', 'SPO-BRF4956-CAT107075-177070:407360:407359:217683', 'SPO-SEA3104-CAT107115-134148:304647:304648:165976', 'SPO-FRU7704-CAT155019-474862:1178302:1178301:656346', 'SPO-FRU1

2024-10-16 17:42:22,564 - frubana_app - DEBUG - Response: [{'sku': 'SPO-FRU1-CAT106983-469411:1170501:1170502:648293', 'quantity': 2000.0}, {'sku': 'SPO-FRU1-CAT106989-457777:1157079:1157080:633375', 'quantity': 200.0}, {'sku': 'SPO-FRU1-CAT106994-181359:423865:423866:223440', 'quantity': 36.0}, {'sku': 'SPO-FRU1-CAT106994-297960:749250:749249:390893', 'quantity': 120.0}, {'sku': 'SPO-FRU1-CAT106994-420594:1076564:1076563:586809', 'quantity': 168.0}, {'sku': 'SPO-FRU1-CAT106996-247611:628902:628901:320745', 'quantity': 168.0}, {'sku': 'SPO-FRU1-CAT106996-247612:628906:628905:320748', 'quantity': 156.0}, {'sku': 'SPO-FRU1-CAT106996-247615:628918:628917:320757', 'quantity': 84.0}, {'sku': 'SPO-FRU1-CAT107269-61529:128314:128313:75002', 'quantity': 185.0}, {'sku': 'SPO-FRU1-CAT107271-60520:128895:128894:75297', 'quantity': 1534.0}, {'sku': 'SPO-FRU1-CAT107271-61001:126729:126728:74240', 'quantity': 2.0}, {'sku': 'SPO-FRU1-CAT107273-473724:1176591:1176592:654586', 'quantity': 340.0}, {'sku

2024-10-16 17:42:23,153 - frubana_app - DEBUG - Response: [{'sku': 'SPO-FRU1-CAT106969-59573:121455:121456:72318', 'quantity': 4000.0}, {'sku': 'SPO-FRU1-CAT106969-59581:121469:121470:72488', 'quantity': 5000.0}, {'sku': 'SPO-FRU1-CAT106976-122678:280566:280565:152144', 'quantity': 1430.0}, {'sku': 'SPO-FRU1-CAT106976-123459:282394:282393:153089', 'quantity': 5184.0}, {'sku': 'SPO-FRU1-CAT106976-231959:591744:591743:296389', 'quantity': 5796.0}, {'sku': 'SPO-FRU1-CAT106976-460710:1159847:1159848:637092', 'quantity': 1000.0}, {'sku': 'SPO-FRU1-CAT106983-469411:1170501:1170502:648293', 'quantity': 14000.0}, {'sku': 'SPO-FRU1-CAT106985-278160:699448:699447:360992', 'quantity': 72.0}, {'sku': 'SPO-FRU1-CAT106985-278161:699452:699451:360995', 'quantity': 80.0}, {'sku': 'SPO-FRU1-CAT106985-278166:699472:699471:361010', 'quantity': 136.0}, {'sku': 'SPO-FRU1-CAT106985-278167:699476:699475:361013', 'quantity': 40.0}, {'sku': 'SPO-FRU1-CAT106985-278170:699488:699487:361022', 'quantity': 28.0}, {

2024-10-16 17:42:23,758 - frubana_app - DEBUG - Response: [] (api_clients.py:387)
2024-10-16 17:42:23,966 - frubana_app - DEBUG - Requesting in transit stock with message: {'skus': ['SPO-FRU1-CAT107026-194566:472172:472171:240410', 'SPO-BRF4956-CAT107075-177070:407360:407359:217683', 'SPO-SEA3104-CAT107115-134148:304647:304648:165976', 'SPO-FRU7704-CAT155019-474862:1178302:1178301:656346', 'SPO-FRU1-CAT106994-469616:1170763:1170762:648603', 'SPO-FRU1-CAT114319-442133:1124242:1124241:615289', 'SPO-FRU1-CAT140017-288675:725544:725543:377280', 'SPO-FRU1-CAT120730-474496:1177818:1177817:655813', 'SPO-FRU1-CAT106980-139971:319718:319717:173913', 'SPO-FRU1-CAT114319-442136:1124447:1124448:615295', 'SPO-FRI3206-CAT111881-133596:303582:303583:165352', 'SPO-PLE7454-CAT107094-292216:733686:733685:382167', 'SPO-FRU1-CAT163043-441912:1123450:1123449:614645', 'SPO-FRU1-CAT107273-473724:1176591:1176592:654586', 'SPO-FRU1-CAT108423-99433:227543:227544:124907', 'SPO-FRU1-CAT120728-474418:1177612:11776

...

2024-10-16 17:42:36,809 - frubana_app - DEBUG - Response: [{'sku': 'SPO-FRU1-CAT106969-60440:125460:125461:73557', 'quantity': 22440.0}, {'sku': 'SPO-FRU1-CAT106985-278159:699444:699443:360989', 'quantity': 40.0}, {'sku': 'SPO-FRU1-CAT106985-278161:699452:699451:360995', 'quantity': 70.0}, {'sku': 'SPO-FRU1-CAT106985-278166:699472:699471:361010', 'quantity': 80.0}, {'sku': 'SPO-FRU1-CAT106985-371910:936998:936997:509492', 'quantity': 280.0}, {'sku': 'SPO-FRU1-CAT106985-371912:937006:937005:509498', 'quantity': 260.0}, {'sku': 'SPO-FRU1-CAT106985-371914:937014:937013:509504', 'quantity': 117.0}, {'sku': 'SPO-FRU1-CAT106994-446769:1133565:1133566:620609', 'quantity': 1794.0}, {'sku': 'SPO-FRU1-CAT106994-468583:1169301:1169302:647187', 'quantity': 6720.0}, {'sku': 'SPO-FRU1-CAT106996-114312:260856:260855:141898', 'quantity': 300.0}, {'sku': 'SPO-FRU1-CAT106996-114313:260860:260859:141901', 'quantity': 196.0}, {'sku': 'SPO-FRU1-CAT106996-114314:260864:260863:141904', 'quantity': 348.0}, {'

2024-10-16 17:42:37,306 - frubana_app - DEBUG - Response: [{'sku': 'SPO-FRU1-CAT106973-465789:1165703:1165704:643499', 'quantity': 24.0}, {'sku': 'SPO-FRU1-CAT106973-97933:223857:223858:122625', 'quantity': 292.0}, {'sku': 'SPO-FRU1-CAT106978-474659:1177943:1177944:655989', 'quantity': 115.0}, {'sku': 'SPO-FRU1-CAT106978-474660:1177945:1177946:655991', 'quantity': 115.0}, {'sku': 'SPO-FRU1-CAT106980-440077:1120051:1120052:612127', 'quantity': 1100.0}, {'sku': 'SPO-FRU1-CAT106980-440080:1120057:1120058:612133', 'quantity': 72.0}, {'sku': 'SPO-FRU1-CAT106980-464931:1164338:1164337:642233', 'quantity': 20.0}, {'sku': 'SPO-FRU1-CAT106980-464934:1164344:1164343:642389', 'quantity': 130.0}, {'sku': 'SPO-FRU1-CAT106980-469624:1170778:1170779:648619', 'quantity': 132.0}, {'sku': 'SPO-FRU1-CAT106987-450726:1142385:1142386:625273', 'quantity': 840.0}, {'sku': 'SPO-FRU1-CAT106989-188059:451944:451943:232189', 'quantity': 4080.0}, {'sku': 'SPO-FRU1-CAT106989-440078:1120054:1120053:612129', 'quanti

2024-10-16 17:42:37,310 - frubana_app - INFO -  ==================================== token: Pk3Zkn7rxDLRN^Hdwg$$ef6h2k!PcT%a ====================================  (api_clients.py:514)


{"start_date": "2024-10-16", "end_date": "2024-10-23", "region": "SPO", "warehouse": "STA", "product_ids": [553851, 108290, 523189, 644680, 620609, 412919, 209365, 173915, 511107, 653149, 175040, 642393, 655561, 412909, 644479, 648631, 553855, 621475, 278359, 623196, 649837, 656399, 604241, 656521, 173919, 466392, 277883, 654467, 320751, 656397, 648741, 656395, 240407, 513470, 165660, 656529, 28, 652849, 644654, 655581, 75842, 356954, 453298, 280, 277876, 649859, 153089, 645678, 572851, 377115, 648637, 377269, 650993, 397295, 633091, 452047, 108420, 638099, 613391, 652847, 654463, 623171, 377137, 635355, 637092, 361013, 623153, 363775, 652238, 408939, 126, 631909, 141907, 553843, 649597, 73168, 376993, 529689, 255289, 654083, 502945, 377284, 628130, 511128, 581679, 638093, 633621, 633095, 320739, 210, 382175, 232192, 180323, 513455, 377267, 108497, 221189, 376869, 376732, 284517, 618341, 523190, 376220, 656220, 576212, 652985, 643429, 656093, 643333, 649291, 654600, 123397, 649809, 130

2024-10-16 17:42:40,284 - frubana_app - INFO - requests_response: [{'id': 652297, 'regionCode': 'SPO', 'warehouse': 'STA', 'forecastDates': [{'quantity': 10.0, 'forecastDate': '2024-10-16'}, {'quantity': 10.0, 'forecastDate': '2024-10-17'}, {'quantity': 13.0, 'forecastDate': '2024-10-18'}, {'quantity': 9.0, 'forecastDate': '2024-10-19'}, {'quantity': 0.0, 'forecastDate': '2024-10-20'}, {'quantity': 5.0, 'forecastDate': '2024-10-21'}, {'quantity': 12.0, 'forecastDate': '2024-10-22'}, {'quantity': 11.0, 'forecastDate': '2024-10-23'}]}, {'id': 647179, 'regionCode': 'SPO', 'warehouse': 'STA', 'forecastDates': [{'quantity': 0.0, 'forecastDate': '2024-10-16'}, {'quantity': 0.0, 'forecastDate': '2024-10-17'}, {'quantity': 0.0, 'forecastDate': '2024-10-18'}, {'quantity': 0.0, 'forecastDate': '2024-10-19'}, {'quantity': 0.0, 'forecastDate': '2024-10-20'}, {'quantity': 0.0, 'forecastDate': '2024-10-21'}, {'quantity': 0.0, 'forecastDate': '2024-10-22'}, {'quantity': 0.0, 'forecastDate': '2024-10-

In [12]:
# Paso 4: Usar los payloads generados
# Puedes imprimir los payloads generados para ver la salida
print(json.dumps(origin_payload, indent=4))

[
    {
        "sku": "SPO-FRU1-CAT107026-194566:472172:472171:240410",
        "warehouse": "GRU",
        "desired_service_level": 0.88,
        "days_to_next_review": 7,
        "units_per_product_dim": 1,
        "supplier_dim_to_product_dim_conversion_factor": 1.0,
        "current_inventory": 511,
        "detailed_incoming_inventory": {
            "2024-10-21": 540.0
        },
        "forecast": {
            "2024-10-16": 30.0,
            "2024-10-17": 23.0,
            "2024-10-18": 23.0,
            "2024-10-19": 11.0,
            "2024-10-20": 0.0,
            "2024-10-21": 14.0,
            "2024-10-22": 29.0,
            "2024-10-23": 22.0
        },
        "forecast_error_model": {
            "distribution": "NORM",
            "mu": 3.3,
            "sigma": 10.625
        },
        "current_price_per_unit": 7.97,
        "percentage_cost_per_unit_excess": 100.0,
        "percentage_cost_per_unit_shortage": 30.0,
        "mandatory": false,
        "suppliers": [

In [13]:
print(json.dumps(destination_payload, indent=4))

[
    {
        "sku": "SPO-FRU7704-CAT107094-399312:1002562:1002561:553851",
        "warehouse": "STA",
        "desired_service_level": 0.9,
        "days_to_next_review": 3,
        "units_per_product_dim": 1,
        "supplier_dim_to_product_dim_conversion_factor": 1.0,
        "current_inventory": 0,
        "detailed_incoming_inventory": {},
        "forecast": {
            "2024-10-16": 0.0,
            "2024-10-17": 0.0,
            "2024-10-18": 0.0,
            "2024-10-19": 0.0,
            "2024-10-20": 0.0,
            "2024-10-21": 0.0,
            "2024-10-22": 0.0,
            "2024-10-23": 0.0
        },
        "forecast_error_model": {
            "distribution": "NORM",
            "mu": 0,
            "sigma": 0.0001
        },
        "current_price_per_unit": 32.5,
        "percentage_cost_per_unit_excess": 100.0,
        "percentage_cost_per_unit_shortage": 30.0,
        "mandatory": false,
        "suppliers": [
            {
                "external_id": {
